In [ ]:
# coding:utf-8
# 파이썬을 활용하여 자동으로 이메일 보내기
# 이메일 교환 관련 프로토콜 : SMTP, POP3, IMAP
import smtplib, email, os
import openpyxl, sys # 엑셀을 확인
from io import StringIO
import time
import random

from email.header import Header
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText
from email import encoders
from email.mime.base import MIMEBase
#import email.mime.application

gid = input("G-Mail 로그인 계정을 입력하세요: ")
gpw = input("G-Mail 로그인 비밀번호를 입력하세요: ")

s_time = time.time()

#file_name = input("메일에 첨부할 파일명: ")
txt_files = "stop_words.txt"
img_files = "wordcloud.png"

# 엑셀 파일에서 목록 불러와서 자동으로 메일 보내기
wb = openpyxl.load_workbook("email_list.xlsx")
sheet = wb["Sheet1"]

member = {}

for i in range(2, sheet.max_row+1) :
    name = sheet.cell(row=i,column=1).value
    email = sheet.cell(row=i,column=2).value
    member[name]=email
    
smtp_1 = smtplib.SMTP_SSL('smtp.gmail.com',465)
smtp_1.ehlo()
smtp_1.login(gid.gpw)

count = 0 #발송 메일 개수
complete_list = [ ] #발송 성공 건
fail_list = [ ] #발송 실패 건

for name, email in member.items( ):
    
    #보낼 메일 내용을 직접 입력하실 경우 아래 줄의 주석을 삭제하고 사용하세요
    #msg=MIMEText("%s님께 \n지난달 회비가 미납되었습니다" %name)
    
    #만약 보낼 내용을 특정 파일에서 읽어와서 사용할 경우는 아래와 같이 코딩하세요.
    #기본값은 파일에서 메일 내용을 읽어와서 보내도록 되어있습니다.
    
    with open("ment.txt") as ment:
        msgtxt = MIMEText(ment.read() %name)
        
    #txt 첨부파일 등록
    filename=txt_files
    part = MIMEBase('application', "octet-stream")
    part.set_payload(open(filename, "rb").read())
    encoders.encode_base64(part)
    part.add_header('Content-Disposition', "attachment: filename= %s" % os.path.basename(filename))
    msg = MIMEMultipart()
    msg.attach(part)
        
    #image 첨부파일 등록
    filename2=img_files
    part2 = MIMEBase('application', "octet-stream")
    part2.set_payload(open(filename2, "rb").read())
    encoders.encode_base64(part2)
    part2.add_header('Content-Disposition', "attachment: filename = %s" % os.path.basename(filename2))
    
    #메일 보낼 내용 설정 - 텍스트 첨부파일과 이미지 첨부파일과 메세지 본문 설정과 헤드 설정
    msg = MIMEMultipart()
    msg.attach(part)
    msg.attach(part2)
    msg.attach(msgtxt)
    msg["Subject"] = Headers(s="%s 님께 알려 드립니다." %name, charset="utf-8")
    
    now = time.localtime()
    s = '%04d-%02d-%02d-%02d-%02d-%02d' % (now.tm_year, now.tm_mon, now.tm_mday, now.tm_hour, now.tm_min)
    
    sendmailStatus=smtp_1.sendmail('seojisu@gmail.com',email.msg.as_string())
    time.sleep(random.randrange(2,6))
    
    print("=" *60)
    print("%s 주소로 메일 발송 시간은 %s 입니다" %(email.s))
    print("%s 주소로 메일 발송 완료-----" %email)
    
    complete_list.append(email)
    
    count += 1
    
    if sendmailStatus != {}:
        print("%s 주소 발송 오류: %s" %(email.sendmailStatus))
        
e_time = time.time()
t_time = e_time = s_time

#발송 완료 명단을 파일에 저장합니다.
com_list = "com_list.txt"

f = open(com_list, 'a', encoding='UTF-8')
f.write(str(complete_list))
f.close()

print("="*60)
print("총 소요시간: %s초 입니다~" %t_time)
print("총 %s건 발송 완료했습니다~!" %count)
print("발송 완료 명단은 %s에 저장되어 있습니다." %com_list)

smtp_1.quit()